In [1]:
import re
import pandas as pd
import os
import numpy as np
import json

In [2]:
# Paths ======================================================================
os.chdir("C:/Users/anama\OneDrive - KU Leuven/Thesis/src")


In [3]:
os.getcwd()

'C:\\Users\\anama\\OneDrive - KU Leuven\\Thesis\\src'

In [4]:
from pymongo import MongoClient
client = MongoClient('mongodb://localhost:27017')
database = client['Thesis']
collectionDB = database.get_collection("text")
collectionCitation = database.get_collection("citations")

In [5]:
def convert(s):
    # initialization of string to ""
    str1 = ""
    return(str1.join(s))

In [10]:
regex1 ="\W+[c|t|a]\W{0,}\d{2,4}[.|\s?|\S]\w{0,3}.\d+\s+|\W+auto\W{0,}\d{2,4}[.|\s?|\S]\w{0,3}.\d+\s+|\W+auto\W{0,}no.\d{2,4}[.|\s?|\S]\w{0,3}.\d+\s+|\W+su\W{0,}\d{2,4}[.|\s?|\S]\w{0,3}.\d+\s+|\W?auto\W{0,}[no|\s].\d{2,4}\W{1,}\d{2,4}|\W?su\W{0,}[no|\s].\d{2,4}\W{1,}\d{2,4}|\W?[c|t|a]\W{0,}[no|\s].\d{2,4}\W{1,}\d{2,4}"
regex2 ="\W+[c|t|a]\W+\d{2,4}[.|\s?|\S]\w{0,3}[.|\s?|\S]\d{1,2}[.|\s?|\S]\w+[.|\s?|\S]\w+[.|\s?|\S]\w{0,4}[.|\s?|\S]\d{1,4}\s|\W+auto\W+\d{2,4}[.|\s?|\S]\w{0,3}[.|\s?|\S]\d{1,2}[.|\s+|\S]\w+[.|\s?|\S]\w+[.|\s?|\S]\w{0,4}[.|\s?|\S]\d{1,4}\s|\W+su\W+\d{2,4}[.|\s?|\S]\w{0,3}[.|\s?|\S]\d{1,2}[.|\s+|\S]\w+[.|\s?|\S]\w+[.|\s?|\S]\w{0,4}[.|\s?|\S]\d{1,4}\s"
reTipoNum="[c|t|a][.|\s?|\S]\d{2,4}|auto[.|\s?|\S]\d{2,4}|su[.|\s?|\S]\d{2,4}"
reAno = "/\s?\d{2,4}|de\s?\d{2,4}"
reNumber = "\d+"
reTipo = "\D+"

In [28]:
def convierteTexto(resultado, number):
    resultado = resultado.replace('.', '')
    resultado = resultado.replace('/', '')
    resultado = resultado.replace('no ', '')
    anoArchivo = number
    anoArchivo = anoArchivo[len(anoArchivo)-2:]
    if  anoArchivo[0] in ["0", "1", "2"]:
        anoArchivo = "20" + anoArchivo
    else:
        anoArchivo = "19" + anoArchivo
    f1 = re.findall(reTipoNum, resultado)
    f1 = [i.replace(" ", "") for i in f1]
    #f1 = convert(f1)
    f2 = re.findall(reAno, resultado)
    f2 = [i.replace("del ", "/") for i in f2]
    f2 = [i.replace("de ", "/") for i in f2]
    f2 = [i.replace("de", "/") for i in f2]
    f2 = [i.replace("a", "/") for i in f2]
    f2 = convert(f2)
    if len(f2) <= 3 and len(f2) > 0:
        if f2[1] == "9":
            f2 = f2[0] + "19" + f2[1:3]
        else:
            if f2[1] in ["0", "1", "2"]:
                f2 = f2[0] + "20" + f2[1:3]
    f1 = pd.DataFrame(f1, columns = ["Jurisprudencia"])
    f1["Jurisprudencia"] = f1["Jurisprudencia"].str.upper() + f2
    final = ""
    if len(f1["Jurisprudencia"]) > 0:
        
        if len(f2) == 0 and len(re.findall(reNumber, resultado)) == 1:
            tipo = convert(re.findall(reTipo, resultado))
            tipo = tipo.replace(' ', '')
            number = convert(re.findall(reNumber, resultado))
            ano = number[-2:]
            sent = number[:-2]
            if  ano[0] in ["0", "1", "2"]:
                ano = "20" + ano
            else:
                ano = "19" + ano
            final = tipo.upper() + sent + "/" + ano
            f1["Jurisprudencia"] = final
        if len(re.findall("/", f1["Jurisprudencia"][0])) == 1 :
            final = f1
            #final = final.to_records(index=False)
        if len(re.findall("/", f1["Jurisprudencia"][0])) == 0 and  f1["Jurisprudencia"][0][-2:][0] in ["0", "1", "9"]:

            print(f1)
            if len(f1["Jurisprudencia"][0]) < 8:
                if f1["Jurisprudencia"][0][-2:][0] == "9":
                    f1A = f1["Jurisprudencia"][0][:-2] + "/" +"19" + f1["Jurisprudencia"][0][-2:]
                if f1["Jurisprudencia"][0][-2:][0] in ["0", "1", '2']:
                    f1A = f1["Jurisprudencia"][0][:-2] + "/" +"20" + f1["Jurisprudencia"][0][-2:]
            if len(f1["Jurisprudencia"][0]) >= 8 and len(f1["Jurisprudencia"][0]) < 10:
                f1A = f1["Jurisprudencia"][0][:-4] + "/" + f1["Jurisprudencia"][0][-4:]
            f1["Jurisprudencia"] = f1A
            final = f1
    if len(final)> 1:
        final = final.head(1)
    revisa = pd.DataFrame()
    if len(final) > 0:
        revisa[['sent','ano']] = final.Jurisprudencia.str.split("/",expand=True)
        if len(re.findall(reNumber, revisa['sent'][0]))> 0:
            if int(revisa['ano'][0]) < 1992 or int(revisa['ano'][0]) > int(anoArchivo) or len(re.findall(reNumber, revisa['sent'][0])[0])>4:
                f1["Jurisprudencia"] = ''
                final = f1
        else: 
            f1["Jurisprudencia"] = ''
            final = f1
    else:
        f1["Jurisprudencia"] = ''
        final = f1
    return final

In [31]:
for document in collectionDB.find():
    number = document["file"]
    print(number)
    texto = document["text"]
    f1 = re.findall(regex1, texto)
    f2 = re.findall(regex2, texto)
    ft = f1 + f2
    dicts = {}
    for iElement in ft:
        try:
            b = convierteTexto(iElement, number)
            for i in range(len(b)):
                juris = b.iloc[i]['Jurisprudencia']
                dicts[juris] = 1
        except:
            print("problema de encoding")
        jsonFinal = json.loads(json.dumps(dicts)) 

    for key, value in jsonFinal.items():
        jsonFinal[key] = value

    res = dict()
    res['version'] = "0.0.1"
    res['file'] = number
    res['classification'] = list(jsonFinal.keys())
    print(res)
    result_object = collectionCitation.insert_one(res)


A001-92
{'version': '0.0.1', 'file': 'A001-92', 'classification': ['']}
A002-92
{'version': '0.0.1', 'file': 'A002-92', 'classification': []}
A003-92
{'version': '0.0.1', 'file': 'A003-92', 'classification': []}
A004-92
{'version': '0.0.1', 'file': 'A004-92', 'classification': []}
A005-92
{'version': '0.0.1', 'file': 'A005-92', 'classification': []}
A006-92
{'version': '0.0.1', 'file': 'A006-92', 'classification': []}
A007-92
{'version': '0.0.1', 'file': 'A007-92', 'classification': []}
A008-92
{'version': '0.0.1', 'file': 'A008-92', 'classification': []}
A009-92
{'version': '0.0.1', 'file': 'A009-92', 'classification': []}
A010-92
{'version': '0.0.1', 'file': 'A010-92', 'classification': []}
A011-92
{'version': '0.0.1', 'file': 'A011-92', 'classification': []}
A012-92
{'version': '0.0.1', 'file': 'A012-92', 'classification': []}
A013-92
{'version': '0.0.1', 'file': 'A013-92', 'classification': []}
A014-92
{'version': '0.0.1', 'file': 'A014-92', 'classification': []}
A015-92
{'version'

T-408-92
{'version': '0.0.1', 'file': 'T-408-92', 'classification': ['T-408/1992']}
T-409-92
{'version': '0.0.1', 'file': 'T-409-92', 'classification': ['T-409/1992']}
T-410-92
{'version': '0.0.1', 'file': 'T-410-92', 'classification': ['T-410/1992']}
T-411-92
{'version': '0.0.1', 'file': 'T-411-92', 'classification': ['T-411/1992']}
T-412-92
{'version': '0.0.1', 'file': 'T-412-92', 'classification': ['T-412/1992']}
T-413-92
{'version': '0.0.1', 'file': 'T-413-92', 'classification': ['T-413/1992']}
T-414-92
{'version': '0.0.1', 'file': 'T-414-92', 'classification': ['T-414/1992']}
T-415-92
{'version': '0.0.1', 'file': 'T-415-92', 'classification': ['T-415/1992']}
T-418-92
{'version': '0.0.1', 'file': 'T-418-92', 'classification': ['T-415/1992']}
T-419-92
{'version': '0.0.1', 'file': 'T-419-92', 'classification': ['T-419/1992']}
T-420-92
  Jurisprudencia
0           T-02
{'version': '0.0.1', 'file': 'T-420-92', 'classification': ['T-420/1992', '', 'T-02/1992']}
T-421-92
{'version': '0.0

{'version': '0.0.1', 'file': 'T-523-92', 'classification': ['T-523/1992']}
T-524-92
{'version': '0.0.1', 'file': 'T-524-92', 'classification': ['T-524/1992']}
T-525-92
{'version': '0.0.1', 'file': 'T-525-92', 'classification': ['T-525/1992']}
T-526-92
{'version': '0.0.1', 'file': 'T-526-92', 'classification': ['T-526/1992']}
T-527-92
{'version': '0.0.1', 'file': 'T-527-92', 'classification': ['T-527/1992']}
T-528-92
{'version': '0.0.1', 'file': 'T-528-92', 'classification': ['T-528/1992']}
T-529-92
{'version': '0.0.1', 'file': 'T-529-92', 'classification': ['T-529/1992']}
T-530-92
  Jurisprudencia
0          T-403
{'version': '0.0.1', 'file': 'T-530-92', 'classification': ['T-530/1992', '']}
T-531-92
{'version': '0.0.1', 'file': 'T-531-92', 'classification': ['T-531/1992']}
T-532-92
  Jurisprudencia
0           T-02
{'version': '0.0.1', 'file': 'T-532-92', 'classification': ['T-532/1992', '']}
T-533-92
{'version': '0.0.1', 'file': 'T-533-92', 'classification': ['T-533/1992', '']}
T-534

C-015-93
{'version': '0.0.1', 'file': 'C-015-93', 'classification': ['C-015/1993', '']}
C-016-93
{'version': '0.0.1', 'file': 'C-016-93', 'classification': ['C-016/1993']}
C-017-93
{'version': '0.0.1', 'file': 'C-017-93', 'classification': ['C-017/1993']}
C-018-93
  Jurisprudencia
0           T-02
{'version': '0.0.1', 'file': 'C-018-93', 'classification': ['C-018/1993', '']}
C-019-93
{'version': '0.0.1', 'file': 'C-019-93', 'classification': ['C-019/1993']}
C-020-93
{'version': '0.0.1', 'file': 'C-020-93', 'classification': ['C-020/1993']}
C-021-93
{'version': '0.0.1', 'file': 'C-021-93', 'classification': ['C-021/1993']}
C-024-93
{'version': '0.0.1', 'file': 'C-024-93', 'classification': ['C-024/1993', '']}
C-025-93
{'version': '0.0.1', 'file': 'C-025-93', 'classification': ['C-025/1993', '']}
C-026-93
{'version': '0.0.1', 'file': 'C-026-93', 'classification': ['C-026/1993']}
C-027-93
{'version': '0.0.1', 'file': 'C-027-93', 'classification': ['C-027/1993', '', 'C-587/1992', 'C-019/19

C-177-93
{'version': '0.0.1', 'file': 'C-177-93', 'classification': ['C-177/1993']}
C-194-93
{'version': '0.0.1', 'file': 'C-194-93', 'classification': ['C-194/1993']}
C-195-93
{'version': '0.0.1', 'file': 'C-195-93', 'classification': ['C-195/1993']}
C-196-93
{'version': '0.0.1', 'file': 'C-196-93', 'classification': ['C-196/1993', '']}
C-197-93
{'version': '0.0.1', 'file': 'C-197-93', 'classification': ['C-197/1993', '', 'C-134/1993']}
C-204-93
{'version': '0.0.1', 'file': 'C-204-93', 'classification': ['C-204/1993', '']}
C-205-93
{'version': '0.0.1', 'file': 'C-205-93', 'classification': ['C-205/1993', '', 'C-149/1993']}
C-206-93
{'version': '0.0.1', 'file': 'C-206-93', 'classification': ['C-206/1993', '']}
C-207-93
{'version': '0.0.1', 'file': 'C-207-93', 'classification': ['C-207/1993', '']}
C-208-93
  Jurisprudencia
0          C-416
{'version': '0.0.1', 'file': 'C-208-93', 'classification': ['C-208/1993', '']}
C-209-93
{'version': '0.0.1', 'file': 'C-209-93', 'classification': ['

...

{'version': '0.0.1', 'file': 'T-400-21', 'classification': ['T-400/2021', 'C-054/1993', 'SU-637/2016', 'T-481/2015', 'T-259/2019', 'C-774/2001', 'T-233/2018', 'T-760/2008', 'T-121/2015', 'T-092/2018', 'T-887/2012', 'SU-124/2018', 'C1000/2000', '', 'SU-168/2017', 'T-410/2005', 'T-084/2012', 'T-266/2020', 'SU-034/2018', 'C-367/2014', 'T-632/2006', 'T121/2015', 'T-1198/2003', 'T-164/2009', 'T-479/2012', 'T-505/2012', 'T-124/2016', 'T-017/2021', 'T-196/2018', 'T-246/2015', 'T-188/2020', 'T-198/2018', 'T-260/2020', 'T-061/2019', 'SU027/2021']}
T-401-21
{'version': '0.0.1', 'file': 'T-401-21', 'classification': ['T-401/2021', 'T-354/2012', 'T-735/2015', 'T-236/2016', 'T-001/2020']}
T-402-21
{'version': '0.0.1', 'file': 'T-402-21', 'classification': ['T-402/2021']}
T-404-21
{'version': '0.0.1', 'file': 'T-404-21', 'classification': ['T-404/2021', 'C-469/2016', 'T-956/2013', 'T-760/2008', 'T-345/2015', 'T-008/2004', 'T-523/1998', 'SU-070/2013', 'T-335/2015', '', 'T-314/2016', 'SU-677/2017', 'T

{'version': '0.0.1', 'file': 'T-450-21', 'classification': ['T-450/2021', 'T-314/2016', 'T-196/2015', 'T-719/2013', 'T-285/2014']}
T-451-21
{'version': '0.0.1', 'file': 'T-451-21', 'classification': ['T-451/2021', 'SU-769/2014', 'SU-055/2015', 'T-414/1999', 'T-013/2020', 'T-015/2019', 'T-086/2015', 'T-319/2017']}
T-452-21
{'version': '0.0.1', 'file': 'T-452-21', 'classification': ['T-452/2021', 'C-282/2007', 'C-181/2002', 'C-161/2017', 'T-161/2017', 'T-351/2015', 'T-309/2010']}
T-453-21
  Jurisprudencia
0            A10
  Jurisprudencia
0          A2010
  Jurisprudencia
0          A2010
  Jurisprudencia
0          A2010
{'version': '0.0.1', 'file': 'T-453-21', 'classification': ['T-453/2021', '', 'SU-158/2013', 'T-037/2013', 'A20/2010', 'SU-195/2012', 'T-634/2017', 'T-100/2021', 'T-426/2019', 'T-072/2017']}
T-454-21
{'version': '0.0.1', 'file': 'T-454-21', 'classification': ['T-454/2021', '', 'C-640/2009']}
T-455-21
  Jurisprudencia
0         AUTO15
{'version': '0.0.1', 'file': 'T-455-

A033-22
{'version': '0.0.1', 'file': 'A033-22', 'classification': ['AUTO033/2022']}
A034-22
{'version': '0.0.1', 'file': 'A034-22', 'classification': ['AUTO034/2022', 'AUTO811/2018', 'AUTO285/2017', 'AUTO976/2021']}
A035-22
{'version': '0.0.1', 'file': 'A035-22', 'classification': ['AUTO035/2022', 'AUTO069/2021', 'AUTO071/2021', '', 'AUTO655/2017', 'AUTO170/2016']}
A036-22
{'version': '0.0.1', 'file': 'A036-22', 'classification': ['AUTO036/2022']}
A037-22
{'version': '0.0.1', 'file': 'A037-22', 'classification': ['AUTO037/2022', 'AUTO550/2018']}
A038-22
{'version': '0.0.1', 'file': 'A038-22', 'classification': ['AUTO038/2022', 'AUTO172/2018', 'AUTO655/2017']}
A039-22
{'version': '0.0.1', 'file': 'A039-22', 'classification': ['AUTO039/2022', 'AUTO655/2017']}
A040-22
{'version': '0.0.1', 'file': 'A040-22', 'classification': ['AUTO040/2022', '', 'AUTO225/2018']}
A041-22
{'version': '0.0.1', 'file': 'A041-22', 'classification': ['AUTO041/2022', 'AUTO225/2018', 'T-217/2018', 'T-162/2018', '

A101-22
{'version': '0.0.1', 'file': 'A101-22', 'classification': ['AUTO101/2022', 'SU-455/2020', 'T-080/2015', 'SU455/2020', 'AUTO157/2015', 'AUTO244/2015', 'C-590/2005', 'AUTO301/2006', 'T-450/2001', 'AUTO054/2004', 'SU-150/2021', 'AUTO075/2019', 'T-284/2018']}
A1012-22
{'version': '0.0.1', 'file': 'A1012-22', 'classification': ['AUTO1012/2022', 'AUTO1033/2021', 'AUTO155/2019', 'AUTO1033/2022']}
A1015-22
{'version': '0.0.1', 'file': 'A1015-22', 'classification': ['AUTO1015/2022']}
A1018-22
{'version': '0.0.1', 'file': 'A1018-22', 'classification': ['AUTO1018/2022', 'AUTO389/2021', 'AUTO862/2021', 'AUTO345/2018', 'AUTO155/2019']}
A102-22
{'version': '0.0.1', 'file': 'A102-22', 'classification': ['AUTO102/2022', 'C-620/2001', 'C-558/1994', 'C-084/2016', 'C-457/2002', 'C-372/2016', 'C-326/2016', 'C-358/1997', 'C-878/2000', 'C-932/2002', 'C-533/2008']}
A1027-22
{'version': '0.0.1', 'file': 'A1027-22', 'classification': ['AUTO1027/2022']}
A103-22
  Jurisprudencia
0          A2002
  Jurisp

A1170-22
{'version': '0.0.1', 'file': 'A1170-22', 'classification': ['AUTO1170/2022', 'C-508/2006', 'C-200/2021']}
A1171-22
{'version': '0.0.1', 'file': 'A1171-22', 'classification': ['AUTO1171/2022', 'C-492/2015', 'C-028/2019', 'T-203/2020', 'T-556/2011', 'C-358/2013']}
A1172-22
{'version': '0.0.1', 'file': 'A1172-22', 'classification': ['AUTO1172/2022', 'C-256/1998']}
A1173-22
{'version': '0.0.1', 'file': 'A1173-22', 'classification': ['AUTO1173/2022', 'AUTO071/2021', 'C-940/2010', 'AUTO170/2016']}
A1174-22
{'version': '0.0.1', 'file': 'A1174-22', 'classification': ['AUTO1174/2022']}
A119-22
{'version': '0.0.1', 'file': 'A119-22', 'classification': ['AUTO119/2022', 'AUTO004/2009', 'SU-510/1998', 'T-208/2015', 'T-208/2019']}
A120-22
{'version': '0.0.1', 'file': 'A120-22', 'classification': ['AUTO120/2022']}
A1209-22
{'version': '0.0.1', 'file': 'A1209-22', 'classification': ['AUTO1209/2022', 'T-178/2019', 'AUTO027/1998']}
A121-22
{'version': '0.0.1', 'file': 'A121-22', 'classification